In [39]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
from datetime import datetime

In [2]:
df = pd.read_csv('covid19_vaccination_data_US_64.csv')

In [3]:
df.head()

Date  MMWR_week Location  Distributed  Distributed_Janssen  \
0  11/20/2021         46       US    567081775             27398400   
1  11/20/2021         46       CO      9948285               447600   
2  11/20/2021         46       WA     13809255               681200   
3  11/20/2021         46       DE      1848455                81400   
4  11/20/2021         46       MT      1625215                96900   

   Distributed_Moderna  Distributed_Pfizer  Distributed_Unk_Manuf  \
0            217592840           322090535                      0   
1              3794340             5706345                      0   
2              5172680             7955375                      0   
3               733460             1033595                      0   
4               677600              850715                      0   

   Dist_Per_100K  Distributed_Per_100k_12Plus  ...  \
0         170803                       200015  ...   
1         172751                       201543  ...   
2         181345                       212420  ...   
3         189826                       220105  ...   
4         152063                       177116  ...   

   Administered_Dose1_Recip_5PlusPop_Pct  Series_Complete_5Plus  \
0                                   73.6            196119179.0   
1                                   74.6              3612834.0   
2                                   76.3              4920505.0   
3                                   75.5               593369.0   
4                                   62.6               551251.0   

   Series_Complete_5PlusPop_Pct  Administered_5Plus  Admin_Per_100k_5Plus  \
0                          62.8         449912252.0              144080.0   
1                          66.6           8365665.0              154162.0   
2                          68.7          11076182.0              154729.0   
3                          64.6           1386361.0              150848.0   
4                          54.7           1295704.0              128590.0   

   Distributed_Per_100k_5Plus  Series_Complete_Moderna_5Plus  \
0                    181603.0                     71609210.0   
1                    183327.0                      1353761.0   
2                    192909.0                      1786017.0   
3                    201128.0                       215854.0   
4                    161292.0                       224266.0   

   Series_Complete_Pfizer_5Plus  Series_Complete_Janssen_5Plus  \
0                   108643416.0                     15741770.0   
1                     1970893.0                       286363.0   
2                     2712390.0                       419439.0   
3                      324584.0                        52397.0   
4                      276683.0                        49946.0   

   Series_Complete_Unk_Manuf_5Plus  
0                         124783.0  
1                           1817.0  
2                           2659.0  
3                            534.0  
4                            356.0  

[5 rows x 80 columns]

In [4]:
df_group = df.groupby(['Date','Location'],as_index=False).agg({"Admin_Per_100K":"sum"})

In [24]:
df_group.tail()

Date Location  Admin_Per_100K
22163  12/31/2020       VT            1962
22164  12/31/2020       WA             841
22165  12/31/2020       WI             952
22166  12/31/2020       WV            2948
22167  12/31/2020       WY             823

In [13]:
def get_cases_by_date(date,df):
    temp = df[df['Date']==date]
    return temp[['Location','Admin_Per_100K']]

In [25]:
cases = get_cases_by_date('12/31/2020',df_group) 

In [26]:
x = cases['Location']
y = cases['Admin_Per_100K']

In [28]:
fig = px.choropleth(locations=x, locationmode="USA-states",color=y, scope="usa")

fig.update_layout(
    font_family="Courier New",
    font_color="black",
    title_font_family="Times New Roman",
    title_font_color="black",
)

fig.show()

In [32]:
df_group.sort_values(by=['Date'],inplace=True)

In [51]:
data_slider = []
dates_range = []
for date in sorted(df_group['Date'].unique(),key=lambda date: datetime.strptime(date, "%m/%d/%Y")):
    df_split =  df_group[(df_group['Date']== date)]
    data_each_date = dict(type='choropleth',locations = df_split['Location'],
                        z=df_split['Admin_Per_100K'].astype(float),
                        locationmode='USA-states',
                        colorbar= {'title':'Doses Administered per 100K'})
    data_slider.append(data_each_date)
    dates_range.append(date)
        

        
        
        
steps = []
for i in range(len(data_slider)):
    step = dict(method='restyle',
                args=['visible', [False] * len(data_slider)],
                label='Date {}'.format(dates_range[i]))
    step['args'][1][i] = True
    steps.append(step)

    
sliders = [dict(active=0, pad={"t": 1}, steps=steps)]

layout = dict(title ='Vaccination progress', geo=dict(scope='usa',
                       projection={'type': 'albers usa'}),
              sliders=sliders)

fig =  go.Figure(data=data_slider, layout=layout)


fig.show()
    

In [19]:
df_pivot = df.pivot('Date','Location','Admin_Per_100K')

In [31]:
df_pivot[0]

Location        AK     AL      AR      AS     AZ  BP2      CA      CO      CT  \
Date                                                                            
01/01/2021  2256.0  738.0  1244.0  1835.0  723.0  0.0   948.0  1645.0  1909.0   
01/02/2021  2515.0  800.0  1299.0  1835.0  812.0  0.0  1043.0  1816.0  2110.0   
01/03/2021  2554.0  804.0  1355.0  1835.0  835.0  0.0  1097.0  1847.0  2167.0   
01/04/2021  2589.0  807.0  1355.0  1835.0  908.0  0.0  1143.0  1953.0  2255.0   
01/05/2021  2604.0  821.0  1355.0  1835.0  944.0  0.0  1157.0  1988.0  2485.0   

Location        DC  ...      US      UT      VA  VA2      VI      VT      WA  \
Date                ...                                                        
01/01/2021  1866.0  ...  1257.0   975.0  1056.0  0.0   674.0  2372.0   963.0   
01/02/2021  2136.0  ...  1344.0  1390.0  1107.0  0.0   674.0  2480.0  1083.0   
01/03/2021  2136.0  ...  1400.0  1494.0  1183.0  0.0   674.0  2496.0  1116.0   
01/04/2021  2208.0  ...  1472.0  1526.0  1292.0  0.0   843.0  2557.0  1217.0   
01/05/2021  2246.0  ...  1574.0  1548.0  1529.0  0.0  1006.0  2557.0  1272.0   

Location        WI      WV      WY  
Date                                
01/01/2021  1059.0  2965.0  1185.0  
01/02/2021  1110.0  3069.0  1306.0  
01/03/2021  1150.0  3082.0  1306.0  
01/04/2021  1150.0  3365.0  1322.0  
01/05/2021  1158.0  3634.0  1322.0  

[5 rows x 65 columns]

In [ ]:
df_grouped=df.groupby(['Date','Location']).agg({"Admin_Per_100K":"sum"}).reset_index()

In [ ]:
def get_cases_by_date(date):

In [32]:
x = df_pivot.iloc[0]
print(x.values)

[2256.  738. 1244. 1835.  723.    0.  948. 1645. 1909. 1866.    0. 1136.
 1107.    0.  708. 1278. 1769. 1620.  884.    0. 1298. 1274.  542. 1265.
 1004.    0. 1278.  953. 2016.    0.  837. 1316. 1288. 5322.  661. 1955.
  943. 2528. 1421. 1880. 1038. 1731.  954. 1175. 1022. 1327.  918. 1203.
 1334. 1777.    0.  994. 2924. 1645. 1805. 1257.  975. 1056.    0.  674.
 2372.  963. 1059. 2965. 1185.]
